# Hyper parameter search for TD3+BC

In [1]:
!pip install d3rlpy

In [2]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import itertools
import math
import subprocess
import os
import d3rlpy
# plt.style.use('matplotlibrc')

# from Python.data_sampler import *

## Building an MDPDataset

We first read in a large batch of samples from the file. As `d3rlpy` wants it in the form (observations, actions, rewards, terminal flags), we go ahead and do that. Here's a helper function to get a dataset from a list of chunks of your choosing.

In [3]:
import numpy as np
import torch
import random
import pandas
from Python.data_sampler import *

In [4]:
def get_dataset(chunks : list, batch_size=30000, 
                path="collected_data/rl_det_small.txt") -> d3rlpy.dataset.MDPDataset :
    random.seed(0)
    samples = DataSampler(path_to_data=path)
    samples.setting("coarse")
    states = []
    actions = []
    rewards = []
    next_states = []
    for chunk in chunks:
        samples.use_chunk(chunk)
        samples.read_chunk()
        [statesChunk, actionsChunk, rewardsChunk, nextStatesChunk] = samples.get_batch(batch_size)
        states.append(statesChunk)
        actions.append(actionsChunk)
        rewards.append(rewardsChunk)
        next_states.append(nextStatesChunk)
    states = torch.cat(states)
    actions = torch.cat(actions)
    rewards = torch.cat(rewards)
    next_states = torch.cat(next_states)
    terminals = np.zeros(len(states))
    terminals[::1111] = 1 #episode length 100, change if necessary
    print(states.shape)
    dataset = d3rlpy.dataset.MDPDataset(states.numpy(), 
                                        actions.numpy(), 
                                        rewards.numpy(), terminals)
    return dataset, states.numpy(), actions.numpy(), rewards.numpy()

We can build the dataset from there, just like this, and split into train and test sets.

In [5]:
dataset, states, actions, rewards = get_dataset([i for  i in range(100)], path="../collected_data/rl_purestochastic.txt")

start
[ 0.00000000e+00  7.95731469e+08  1.14110892e-01  2.46000047e-02
 -2.40000134e-02  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
 -6.00000000e-01 -6.00000000e-01 -6.00000000e-01]
Read chunk # 1 out of 4999
start
[ 0.00000000e+00  7.95731469e+08 -4.33891077e-02 -4.23999953e-02
  2.84999866e-02  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
 -5.95938047e-01 -6.00000000e-01 -4.85130982e-02]
Read chunk # 2 out of 4999
start
[ 0.00000000e+00  7.95731469e+08 -3.97089108e-01 -5.19999953e-02
 -1.57000134e-02  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
 -3.84874650e-01  5.98976918e-01 -3.12414656e-01]
Read chunk # 3 out of 4999
start
[ 0.00000000e+00  7.95731469e+08 -3.33189108e-01  1.48000047e-02
  4.99998658e-03  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
  4.33187685e-01  5.18887883e-01  2.92787205e-01]
Read chunk # 4 out of 4999
start
[ 0.00000000e+00  7.95731469e+08  3.58910892e-01 -5.15999953e-02
  1.93999866e-02  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
  6.00000000

start
[ 0.00000000e+00  7.95731469e+08  2.35910892e-01 -5.37999953e-02
 -2.50000134e-02  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
  5.38838169e-01  6.00000000e-01 -3.75898719e-01]
Read chunk # 45 out of 4999
start
[ 0.00000000e+00  7.95731469e+08 -4.08910771e-03  5.96000047e-02
 -2.94000134e-02  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
  6.00000000e-01 -6.00000000e-01 -6.00000000e-01]
Read chunk # 46 out of 4999
start
[ 0.00000000e+00  7.95731469e+08  2.03810892e-01  9.20000469e-03
 -2.18000134e-02  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
  6.00000000e-01 -4.59576187e-01 -6.00000000e-01]
Read chunk # 47 out of 4999
start
[ 0.00000000e+00  7.95731469e+08 -5.44891077e-02 -4.83999953e-02
 -2.32000134e-02  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
 -2.21987424e-01  4.59305017e-01  6.00000000e-01]
Read chunk # 48 out of 4999
start
[ 0.00000000e+00  7.95731469e+08  2.05108923e-02  3.00000469e-03
  4.19998658e-03  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
  6.0000

[ 0.00000000e+00  7.95731469e+08  1.03310892e-01 -3.81999953e-02
 -2.60000134e-02  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
  6.00000000e-01 -6.00000000e-01 -2.81368998e-01]
Read chunk # 93 out of 4999
start
[ 0.00000000e+00  7.95731469e+08  1.46510892e-01 -4.51999953e-02
  3.79998658e-03  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
  1.45187554e-01 -4.01614005e-01  4.47809157e-01]
Read chunk # 94 out of 4999
start
[ 0.00000000e+00  7.95731469e+08 -2.38389108e-01  3.52000047e-02
  2.49998658e-03  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
  3.52784505e-01  6.00000000e-01  1.80697681e-01]
Read chunk # 95 out of 4999
start
[ 0.00000000e+00  7.95731469e+08  2.94710892e-01  5.04000047e-02
 -9.80001342e-03  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
  1.69246192e-01  6.00000000e-01  6.00000000e-01]
Read chunk # 96 out of 4999
start
[ 0.00000000e+00  7.95731469e+08  1.52510892e-01  4.69199999e-09
  2.15999866e-02  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
  3.82529587e-

In [6]:
print("The behavior policy value statistics are:")
dataset.compute_stats()['return']

The behavior policy value statistics are:


{'mean': -290.4386,
 'std': 158.53566,
 'min': -622.8723,
 'max': 0.0,
 'histogram': (array([ 5,  3,  5,  2,  4,  1,  5,  0,  5,  8, 10,  6, 10,  7,  5,  7,  9,
          7,  0,  1]),
  array([-622.8723  , -591.7287  , -560.5851  , -529.44147 , -498.29785 ,
         -467.15424 , -436.01062 , -404.867   , -373.7234  , -342.57977 ,
         -311.43616 , -280.29254 , -249.14893 , -218.00531 , -186.8617  ,
         -155.71808 , -124.57446 ,  -93.43085 ,  -62.28723 ,  -31.143616,
            0.      ], dtype=float32))}

In [7]:
from sklearn.model_selection import train_test_split
train_episodes, test_episodes = train_test_split(dataset, test_size=0.2)

## Setting up an Algorithm

In [8]:
from d3rlpy.algos import CQL, TD3PlusBC
from d3rlpy.models.encoders import VectorEncoderFactory

from d3rlpy.preprocessing import MinMaxActionScaler
import random
action_scaler = MinMaxActionScaler(minimum=-0.6, maximum=0.6)

from d3rlpy.metrics.scorer import td_error_scorer
from d3rlpy.metrics.scorer import average_value_estimation_scorer
from d3rlpy.metrics.scorer import initial_state_value_estimation_scorer

from d3rlpy.ope import FQE
# metrics to evaluate with
from d3rlpy.metrics.scorer import soft_opc_scorer
import pickle as pkl
from statistics import harmonic_mean as hm

## Perform a random search on hyper params. 

As good fqe on both stochastic and deterministic data is needed for good performance during the evaluation step in the simulator, we take the harmonic mean of both fqes to understand the performance on each dataset. The harmonic mean is large only when each number whose mean is being taken is large. Therefore, a large harmonic mean corresponds to large numbers whose mean is being taken.


In [9]:

# The number of times we would wanna do a random search for hyper-params. In 
# every random search, we randomly pick a new set of hyper-params.
num_search_iterations = 40
largest_fqe = -np.inf

for i in range(num_search_iterations):

    random.seed()

    actor_lr_this_iter = random.uniform(1e-5, 1e-2)
    critic_lr_this_iter = random.uniform(1e-5, 1e-2)
    temp_lr_this_iter = random.uniform(1e-5, 1e-4)
    n_steps_this_iter = random.choice([1, 3, 5, 7])

    actor_encoder = VectorEncoderFactory(hidden_units=[12, 24, 36, 24, 12],
                                          activation='relu', use_batch_norm=True, dropout_rate=0.2)
    critic_encoder = VectorEncoderFactory(hidden_units=[12, 24, 24, 12],
                                          activation='relu', use_batch_norm=True, dropout_rate=0.2)

    print("search iteration: ", i)
    print("using hyper params: ", [actor_lr_this_iter, critic_lr_this_iter, 
                                   temp_lr_this_iter, n_steps_this_iter])

    model = TD3PlusBC(q_func_factory='qr', #qr -> quantile regression q function, but you don't have to use this
                reward_scaler='standard',
#                 actor_encoder_factory = actor_encoder,
#                 critic_encoder_factory = critic_encoder,
                action_scaler=action_scaler,
                actor_learning_rate=actor_lr_this_iter, 
                critic_learning_rate=critic_lr_this_iter,
                n_steps=n_steps_this_iter, 
                use_gpu=True) #change it to true if you have one
    model.build_with_dataset(dataset)

    model.fit(train_episodes,
        eval_episodes=test_episodes,
        n_epochs=50, 
        tensorboard_dir='runs',
        scorers={
            'td_error': td_error_scorer,
            'init_value': initial_state_value_estimation_scorer,
            'ave_value': average_value_estimation_scorer
        })
    
    ope_dataset, states_ope, actions_ope, rewards_ope = get_dataset([i+100 for i  in range(20)], 
                                                                    path="../collected_data/rl_stochpid.txt") #change if you'd prefer different chunks
    ope_train_episodes, ope_test_episodes = train_test_split(ope_dataset, test_size=0.2)

    fqe = FQE(algo=model, action_scaler = action_scaler, use_gpu=True) #change this if you have one!
    history_stoch = fqe.fit(ope_train_episodes,
        eval_episodes=ope_test_episodes,
        tensorboard_dir='runs',
        n_epochs=50, n_steps_per_epoch=1000, #change if overfitting/underfitting
        scorers={
           'init_value': initial_state_value_estimation_scorer,
            'ave_value': average_value_estimation_scorer,
           'soft_opc': soft_opc_scorer(return_threshold=0)
        })
    
    ope_dataset, states_ope, actions_ope, rewards_ope = get_dataset([i+200 for i in range(40)], 
                                                                    path="../collected_data/rl_purestochastic.txt") #change if you'd prefer different chunks
    ope_train_episodes, ope_test_episodes = train_test_split(ope_dataset, test_size=0.2)

    fqe = FQE(algo=model, action_scaler = action_scaler, use_gpu=True) #change this if you have one!
    history_det = fqe.fit(ope_train_episodes,
        eval_episodes=ope_test_episodes,
        tensorboard_dir='runs',
        n_epochs=50, n_steps_per_epoch=1000, #change if overfitting/underfitting
        scorers={
           'init_value': initial_state_value_estimation_scorer,
            'ave_value': average_value_estimation_scorer,
           'soft_opc': soft_opc_scorer(return_threshold=0)
        })
    
    if(hm([history_stoch[-1][1]["ave_value"] + 50, 
           history_det[-1][1]["ave_value"] + 50]) \
                                                          > largest_fqe):
        largest_fqe = hm([history_stoch[-1][1]["ave_value"] + 50, 
                         history_det[-1][1]["ave_value"] + 50])

        # Save the hyper-params
        hyperparams = [actor_lr_this_iter, critic_lr_this_iter, 
                       temp_lr_this_iter, n_steps_this_iter]

        with open("hyperparams_td3bc.pkl", "wb") as f:
            print("most optimal hyper params for td3+bc at this point: ", hyperparams)
            pkl.dump(hyperparams, f)

        # Save model and policy
        model.save_model("model_hyperparams_td3bc.pt")
        model.save_policy("policy_hyperparams_td3bc.pt")


search iteration:  0
using hyper params:  [0.0037731556128830085, 0.007522776116996934, 6.821776549135187e-05, 7]
2022-04-21 21:27.18 [debug    ] RoundIterator is selected.
2022-04-21 21:27.18 [info     ] Directory is created at d3rlpy_logs/TD3PlusBC_20220421212718
2022-04-21 21:27.18 [debug    ] Fitting scaler...              scaler=standard
2022-04-21 21:27.18 [debug    ] Fitting action scaler...       action_scaler=min_max
2022-04-21 21:27.18 [debug    ] Fitting reward scaler...       reward_scaler=standard
2022-04-21 21:27.18 [warning  ] Skip building models since they're already built.
2022-04-21 21:27.18 [info     ] Parameters are saved to d3rlpy_logs/TD3PlusBC_20220421212718/params.json params={'action_scaler': {'type': 'min_max', 'params': {'minimum': array(-0.6), 'maximum': array(0.6)}}, 'actor_encoder_factory': {'type': 'default', 'params': {'activation': 'relu', 'use_batch_norm': False, 'dropout_rate': None}}, 'actor_learning_rate': 0.0037731556128830085, 'actor_optim_factor

Epoch 1/50:   0%|          | 0/342 [00:00<?, ?it/s]

2022-04-21 21:27.27 [info     ] TD3PlusBC_20220421212718: epoch=1 step=342 epoch=1 metrics={'time_sample_batch': 0.0003263329901890448, 'time_algorithm_update': 0.020285752781650478, 'critic_loss': 15.660546104810392, 'actor_loss': 3.1024223461485745, 'time_step': 0.020668699727420917, 'td_error': 1.4452426617250906, 'init_value': -12.632340431213379, 'ave_value': -11.535428431906343} step=342
2022-04-21 21:27.27 [info     ] Model parameters are saved to d3rlpy_logs/TD3PlusBC_20220421212718/model_342.pt


Epoch 2/50:   0%|          | 0/342 [00:00<?, ?it/s]

2022-04-21 21:27.34 [info     ] TD3PlusBC_20220421212718: epoch=2 step=684 epoch=2 metrics={'time_sample_batch': 0.00031444552349068266, 'time_algorithm_update': 0.017354576908356963, 'critic_loss': 6.3804334450883475, 'actor_loss': 3.100024694587752, 'time_step': 0.01772191719702113, 'td_error': 1.7499709617873869, 'init_value': -17.590600967407227, 'ave_value': -16.05815606255957} step=684
2022-04-21 21:27.34 [info     ] Model parameters are saved to d3rlpy_logs/TD3PlusBC_20220421212718/model_684.pt


...

2022-04-22 03:55.39 [info     ] FQE_20220422035222: epoch=49 step=16856 epoch=49 metrics={'time_sample_batch': 0.00018850038217943767, 'time_algorithm_update': 0.010939027680907138, 'loss': 0.4795450915685357, 'time_step': 0.011208809392396794, 'init_value': -18.180057525634766, 'ave_value': -14.977134932395934, 'soft_opc': nan} step=16856


2022-04-22 03:55.39 [info     ] Model parameters are saved to d3rlpy_logs/FQE_20220422035222/model_16856.pt


Epoch 50/50:   0%|          | 0/344 [00:00<?, ?it/s]

2022-04-22 03:55.43 [info     ] FQE_20220422035222: epoch=50 step=17200 epoch=50 metrics={'time_sample_batch': 0.00019457381825114406, 'time_algorithm_update': 0.010516940854316535, 'loss': 0.4747186710077966, 'time_step': 0.010789546855660371, 'init_value': -18.271224975585938, 'ave_value': -14.996540300289917, 'soft_opc': nan} step=17200


2022-04-22 03:55.43 [info     ] Model parameters are saved to d3rlpy_logs/FQE_20220422035222/model_17200.pt


## Reading hyper params from file

In [10]:
with open("hyperparams_td3bc.pkl", "rb") as f:
    data = pkl.load(f)

print(data)

[0.005599980063978588, 0.0019551894944399694, 1.1846518566446107e-05, 1]
